

# ハイパーパラメータ最適化の結果を可視化する

Optuna では :mod:`optuna.visualization` モジュールで様々な可視化機能を提供しており、
最適化の結果を視覚的に分析することができます。

なお、本チュートリアルでは [Plotly](https://plotly.com/python)_ のインストールが必要です。

```console
$ pip install plotly

# Jupyter Notebook で本チュートリアルを実行する場合に必要です。
$ pip install nbformat
```
Plotly の代わりに [Matplotlib](https://matplotlib.org/)_ を使用したい場合、以下のコマンドを実行してください:

```console
$ pip install matplotlib
```
本チュートリアルでは、FashionMNIST データセットに対する PyTorch モデルの最適化結果を可視化しながら、
このモジュールの使い方を説明します。

多目的最適化の結果を可視化する場合 (:func:`optuna.visualization.plot_pareto_front` の使用) は、
`multi_objective` のチュートリアルを参照してください。

<div class="alert alert-info"><h4>Note</h4><p>[Optuna Dashboard](https://github.com/optuna/optuna-dashboard)_ を使用すると、
   最適化の履歴やハイパーパラメータの重要度、ハイパーパラメータ間の関係などを
   グラフや表で確認できます。
   最適化結果を保存するには `RDB バックエンド <rdb>` を使用し、
   以下のコマンドを実行して Optuna Dashboard を起動してください。

```console
$ pip install optuna-dashboard
$ optuna-dashboard sqlite:///example-study.db
```
   詳細は [GitHub リポジトリ](https://github.com/optuna/optuna-dashboard)_ をご覧ください。

   .. list-table::
      :header-rows: 1

      * - スタディの管理
        - インタラクティブなグラフで可視化
      * - .. image:: https://user-images.githubusercontent.com/5564044/205545958-305f2354-c7cd-4687-be2f-9e46e7401838.gif
        - .. image:: https://user-images.githubusercontent.com/5564044/205545965-278cd7f4-da7d-4e2e-ac31-6d81b106cada.gif</p></div>


In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision


import optuna

# 以下の例では、`optuna.visualization` を `optuna.visualization.matplotlib` に置き換えることで、
# Plotly の代わりに Matplotlib を使用できます。
from optuna.visualization import plot_contour
from optuna.visualization import plot_edf
from optuna.visualization import plot_intermediate_values
from optuna.visualization import plot_optimization_history
from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_param_importances
from optuna.visualization import plot_rank
from optuna.visualization import plot_slice
from optuna.visualization import plot_timeline


SEED = 13
torch.manual_seed(SEED)

DEVICE = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
DIR = ".."
BATCHSIZE = 128
N_TRAIN_EXAMPLES = BATCHSIZE * 30
N_VALID_EXAMPLES = BATCHSIZE * 10


def define_model(trial):
    n_layers = trial.suggest_int("n_layers", 1, 2)
    layers = []

    in_features = 28 * 28
    for i in range(n_layers):
        out_features = trial.suggest_int("n_units_l{}".format(i), 64, 512)
        layers.append(nn.Linear(in_features, out_features))
        layers.append(nn.ReLU())

        in_features = out_features

    layers.append(nn.Linear(in_features, 10))
    layers.append(nn.LogSoftmax(dim=1))

    return nn.Sequential(*layers)


# モデルの学習と評価を定義します。
def train_model(model, optimizer, train_loader):
    model.train()
    for batch_idx, (data, target) in enumerate(train_loader):
        data, target = data.view(-1, 28 * 28).to(DEVICE), target.to(DEVICE)
        optimizer.zero_grad()
        F.nll_loss(model(data), target).backward()
        optimizer.step()


def eval_model(model, valid_loader):
    model.eval()
    correct = 0
    with torch.no_grad():
        for batch_idx, (data, target) in enumerate(valid_loader):
            data, target = data.view(-1, 28 * 28).to(DEVICE), target.to(DEVICE)
            pred = model(data).argmax(dim=1, keepdim=True)
            correct += pred.eq(target.view_as(pred)).sum().item()

    accuracy = correct / N_VALID_EXAMPLES

    return accuracy

目的関数を定義します。



In [ ]:
def objective(trial):
    train_dataset = torchvision.datasets.FashionMNIST(
        DIR, train=True, download=True, transform=torchvision.transforms.ToTensor()
    )
    train_loader = torch.utils.data.DataLoader(
        torch.utils.data.Subset(train_dataset, list(range(N_TRAIN_EXAMPLES))),
        batch_size=BATCHSIZE,
        shuffle=True,
    )

    val_dataset = torchvision.datasets.FashionMNIST(
        DIR, train=False, transform=torchvision.transforms.ToTensor()
    )
    val_loader = torch.utils.data.DataLoader(
        torch.utils.data.Subset(val_dataset, list(range(N_VALID_EXAMPLES))),
        batch_size=BATCHSIZE,
        shuffle=True,
    )
    model = define_model(trial).to(DEVICE)

    optimizer = torch.optim.Adam(
        model.parameters(), trial.suggest_float("lr", 1e-5, 1e-1, log=True)
    )

    for epoch in range(10):
        train_model(model, optimizer, train_loader)

        val_accuracy = eval_model(model, val_loader)
        trial.report(val_accuracy, epoch)

        if trial.should_prune():
            raise optuna.exceptions.TrialPruned()

    return val_accuracy

In [ ]:
study = optuna.create_study(
    direction="maximize",
    sampler=optuna.samplers.TPESampler(seed=SEED),
    pruner=optuna.pruners.MedianPruner(),
)
study.optimize(objective, n_trials=30, timeout=300)

## プロット関数
最適化履歴を可視化します。詳細は :func:`~optuna.visualization.plot_optimization_history` を参照してください。



In [ ]:
plot_optimization_history(study)

トライアルの学習曲線を可視化します。詳細は :func:`~optuna.visualization.plot_intermediate_values` を参照してください。



In [ ]:
plot_intermediate_values(study)

高次元パラメータの関係を可視化します。詳細は :func:`~optuna.visualization.plot_parallel_coordinate` を参照してください。



In [ ]:
plot_parallel_coordinate(study)

可視化するパラメータを選択します。



In [ ]:
plot_parallel_coordinate(study, params=["lr", "n_layers"])

ハイパーパラメータの関係を可視化します。詳細は :func:`~optuna.visualization.plot_contour` を参照してください。



In [ ]:
plot_contour(study)

可視化するパラメータを選択します。



In [ ]:
plot_contour(study, params=["lr", "n_layers"])

ハイパーパラメータをスライスプロットとして可視化します。詳細は :func:`~optuna.visualization.plot_slice` を参照してください。



In [ ]:
plot_slice(study)

可視化するパラメータを選択します。



In [ ]:
plot_slice(study, params=["lr", "n_layers"])

パラメータの重要度を可視化します。詳細は :func:`~optuna.visualization.plot_param_importances` を参照してください。



In [ ]:
plot_param_importances(study)

ハイパーパラメータの重要度を用いて、トライアルの実行時間に影響を与えているハイパーパラメータを特定します。



In [ ]:
optuna.visualization.plot_param_importances(
    study, target=lambda t: t.duration.total_seconds(), target_name="duration"
)

経験的分布関数を可視化します。詳細は :func:`~optuna.visualization.plot_edf` を参照してください。



In [ ]:
plot_edf(study)

目的値で色分けした散布図でパラメータの関係を可視化します。詳細は :func:`~optuna.visualization.plot_rank` を参照してください。



In [ ]:
plot_rank(study)

実行されたトライアルの最適化タイムラインを可視化します。詳細は :func:`~optuna.visualization.plot_timeline` を参照してください。



In [ ]:
plot_timeline(study)

## 生成された図のカスタマイズ
:mod:`optuna.visualization` および :mod:`optuna.visualization.matplotlib` では、関数が編集可能な図オブジェクトを返します:
モジュールに応じて :class:`plotly.graph_objects.Figure` または :class:`matplotlib.axes.Axes` です。
これにより、ユーザーは可視化ライブラリの API を使用して、生成された図を必要に応じて変更できます。
以下の例では、Plotly ベースの :func:`~optuna.visualization.plot_intermediate_values` で描画された図のタイトルを手動で置き換えています。



In [ ]:
fig = plot_intermediate_values(study)

fig.update_layout(
    title="FashionMNIST 分類のためのハイパーパラメータ最適化",
    xaxis_title="エポック",
    yaxis_title="検証精度",
)